In [3]:
from __future__ import unicode_literals, print_function, division
from io import open
import unicodedata
import string
import re
import random

import torch
import torch.nn as nn
from torch import optim
import torch.nn.functional as F

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")


In [4]:
SOS_token = 0
EOS_token = 1


class Lang:
    def __init__(self, name):
        self.name = name
        self.word2index = {}
        self.word2count = {}
        self.index2word = {0: "SOS", 1: "EOS"}
        self.n_words = 2  # Count SOS and EOS

    def addSentence(self, sentence):
        for word in sentence.split(' '):
            self.addWord(word)

    def addWord(self, word):
        if word not in self.word2index:
            self.word2index[word] = self.n_words
            self.word2count[word] = 1
            self.index2word[self.n_words] = word
            self.n_words += 1
        else:
            self.word2count[word] += 1

In [6]:
# Turn a Unicode string to plain ASCII, thanks to
# http://stackoverflow.com/a/518232/2809427
def unicodeToAscii(s):
    return ''.join(
        c for c in unicodedata.normalize('NFD', s)
        if unicodedata.category(c) != 'Mn'
    )

# Lowercase, trim, and remove non-letter characters


def normalizeString(s):
    s = unicodeToAscii(s.lower().strip())
    s = re.sub(r"([.!?])", r" \1", s)
    s = re.sub(r"[^a-zA-Z.!?]+", r" ", s)
    return s

In [7]:
def readLangs(lang1, lang2, reverse=False):
    print("Reading lines...")

    # Read the file and split into lines
    lines = open('/home/bharat/Downloads/data/%s-%s.txt' % (lang1, lang2), encoding='utf-8').\
        read().strip().split('\n')

    # Split every line into pairs and normalize
    pairs = [[normalizeString(s) for s in l.split('\t')] for l in lines]

    # Reverse pairs, make Lang instances
    if reverse:
        pairs = [list(reversed(p)) for p in pairs]
        input_lang = Lang(lang2)
        output_lang = Lang(lang1)
    else:
        input_lang = Lang(lang1)
        output_lang = Lang(lang2)

    return input_lang, output_lang, pairs

In [8]:
MAX_LENGTH = 10

eng_prefixes = (
    "i am ", "i m ",
    "he is", "he s ",
    "she is", "she s",
    "you are", "you re ",
    "we are", "we re ",
    "they are", "they re "
)


def filterPair(p):
    return len(p[0].split(' ')) < MAX_LENGTH and \
        len(p[1].split(' ')) < MAX_LENGTH and \
        p[1].startswith(eng_prefixes)


def filterPairs(pairs):
    return [pair for pair in pairs if filterPair(pair)]

In [9]:
def prepareData(lang1, lang2, reverse=False):
    input_lang, output_lang, pairs = readLangs(lang1, lang2, reverse)
    print("Read %s sentence pairs" % len(pairs))
    pairs = filterPairs(pairs)
    print("Trimmed to %s sentence pairs" % len(pairs))
    print("Counting words...")
    for pair in pairs:
        input_lang.addSentence(pair[0])
        output_lang.addSentence(pair[1])
    print("Counted words:")
    print(input_lang.name, input_lang.n_words)
    print(output_lang.name, output_lang.n_words)
    return input_lang, output_lang, pairs


input_lang, output_lang, pairs = prepareData('eng', 'fra', True)
print(random.choice(pairs))

Reading lines...
Read 135842 sentence pairs
Trimmed to 10853 sentence pairs
Counting words...
Counted words:
fra 4489
eng 2925
['je romps ce soir avec ma petite copine .', 'i m breaking up with my girlfriend tonight .']


In [10]:
#EncoderRNN
class EncoderRNN(nn.Module):
    
    
    def __init__(self, input_size, hidden_size):
        super(EncoderRNN, self).__init__()
        self.hidden_size = hidden_size
        self.embedding = nn.Embedding(input_size, hidden_size)
        self.gru = nn.GRU(hidden_size,hidden_size)
    
    def forward(self, input, hidden):
        embedded =  self.embedding(input).view(1,1,-1)
        output = embedded
        output, hidden = self.gru(output, hidden)
        return output,hidden
    
    def initHidden(self):
        return torch.zeros(1, 1, self.hidden_size, device=device)

  

In [11]:
#AttnDecoderRNN

class AttnDecoderRNN(nn.Module):
    def __init__(self, hidden_size, output_size, dropout_p = 0.1, max_length = MAX_LENGTH):
        super(AttnDecoderRNN, self).__init__()
        self.hidden_size = hidden_size
        self.output_size = output_size
        self.dropout_p = dropout_p
        self.max_length =  max_length

        self.embedding = nn.Embedding(self.output_size, self.hidden_size)
        #max_length is defined above-- there are sentences of all sizes in the training data, 
        #to actually create(self.attn) and train this layer we have to choose a maximum sentence length 
        
        self.attn = nn.Linear(self.hidden_size * 2, self.max_length)
        self.attn_combine = nn.Linear(self.hidden_size * 2, self.hidden_size)
        self.dropout = nn.Dropout(self.dropout_p)
        self.gru = nn.GRU(self.hidden_size, self.hidden_size)
        self.out = nn.Linear(self.hidden_size, self.output_size)
    
    
    def forward(self, input, hidden, encoder_outputs):
        embedded = self.embedding(input).view(1,1,-1)
        embedded = self.dropout(embedded)
        
       
        
        attn_weights = F.softmax(self.attn(torch.cat((embedded[0], hidden[0]), 1)), dim=1)

        attn_applied = torch.bmm(attn_weights.unsqueeze(0), encoder_outputs.unsqueeze(0))
        
        
        output = torch.cat((embedded[0], attn_applied[0]), 1)
        output = self.attn_combine(output).unsqueeze(0)

        output = F.relu(output)
        output, hidden = self.gru(output, hidden)
        
        output = F.log_softmax(self.out(output[0]), dim=1)
        return output, hidden, attn_weights
        
        
    def initHidden(self):
        return torch.zeros(1, 1, self.hidden_size, device=device)
    

In [12]:
def indexesFromSentence(lang, sentence):
    return [lang.word2index[word] for word in sentence.split(' ')]


def tensorFromSentence(lang, sentence):
    indexes = indexesFromSentence(lang, sentence)
    indexes.append(EOS_token)
    return torch.tensor(indexes, dtype=torch.long, device=device).view(-1, 1)


def tensorsFromPair(pair):
    input_tensor = tensorFromSentence(input_lang, pair[0])
    target_tensor = tensorFromSentence(output_lang, pair[1])
    return (input_tensor, target_tensor)

In [13]:
teacher_forcing_ratio = 0.5


def train(input_tensor, target_tensor, encoder, decoder, encoder_optimizer, decoder_optimizer, criterion, max_length=MAX_LENGTH):
    encoder_hidden = encoder.initHidden()

    encoder_optimizer.zero_grad()
    decoder_optimizer.zero_grad()

    input_length = input_tensor.size(0)
    target_length = target_tensor.size(0)

    encoder_outputs = torch.zeros(max_length, encoder.hidden_size, device=device)

    loss = 0

    for ei in range(input_length):
        encoder_output, encoder_hidden = encoder(
            input_tensor[ei], encoder_hidden)
        ###########################################################################################################
       # print(encoder_output)
        #print("\n\n" )
        #print(encoder_hidden)
        #input()
        #######################################################################################################
        encoder_outputs[ei] = encoder_output[0, 0]

    decoder_input = torch.tensor([[SOS_token]], device=device)

    decoder_hidden = encoder_hidden

    use_teacher_forcing = True if random.random() < teacher_forcing_ratio else False

    if use_teacher_forcing:
        # Teacher forcing: Feed the target as the next input
        for di in range(target_length):
            decoder_output, decoder_hidden, decoder_attention = decoder(
                decoder_input, decoder_hidden, encoder_outputs)
            loss += criterion(decoder_output, target_tensor[di])
            decoder_input = target_tensor[di]  # Teacher forcing

    else:
        # Without teacher forcing: use its own predictions as the next input
        for di in range(target_length):
            decoder_output, decoder_hidden, decoder_attention = decoder(
                decoder_input, decoder_hidden, encoder_outputs)
            topv, topi = decoder_output.topk(1)
            decoder_input = topi.squeeze().detach()  # detach from history as input

            loss += criterion(decoder_output, target_tensor[di])
            if decoder_input.item() == EOS_token:
                break

    loss.backward()

    encoder_optimizer.step()
    decoder_optimizer.step()

    return loss.item() / target_length

In [14]:
import time
import math


def asMinutes(s):
    m = math.floor(s / 60)
    s -= m * 60
    return '%dm %ds' % (m, s)


def timeSince(since, percent):
    now = time.time()
    s = now - since
    es = s / (percent)
    rs = es - s
    return '%s (- %s)' % (asMinutes(s), asMinutes(rs))

In [15]:
def trainIters(encoder, decoder, n_iters, print_every=1000, plot_every=100, learning_rate=0.01):
    start = time.time()
    plot_losses = []
    print_loss_total = 0  # Reset every print_every
    plot_loss_total = 0  # Reset every plot_every

    encoder_optimizer = optim.SGD(encoder.parameters(), lr=learning_rate)
    decoder_optimizer = optim.SGD(decoder.parameters(), lr=learning_rate)
    training_pairs = [tensorsFromPair(random.choice(pairs))
                     
                      for i in range(n_iters)]
    criterion = nn.NLLLoss()

    for iter in range(1, n_iters + 1):
        training_pair = training_pairs[iter - 1]
        input_tensor = training_pair[0]
        target_tensor = training_pair[1]
        ##################################
        #print(input_tensor)
        #print(target_tensor)
        ##############################

        loss = train(input_tensor, target_tensor, encoder,
                     decoder, encoder_optimizer, decoder_optimizer, criterion)
        print_loss_total += loss
        plot_loss_total += loss

        if iter % print_every == 0:
            print_loss_avg = print_loss_total / print_every
            print_loss_total = 0
            print('%s (%d %d%%) %.4f' % (timeSince(start, iter / n_iters),
                                         iter, iter / n_iters * 100, print_loss_avg))

        if iter % plot_every == 0:
            plot_loss_avg = plot_loss_total / plot_every
            plot_losses.append(plot_loss_avg)
            plot_loss_total = 0

    showPlot(plot_losses)

In [16]:
import matplotlib.pyplot as plt
plt.switch_backend('agg')
import matplotlib.ticker as ticker
import numpy as np


def showPlot(points):
    plt.figure()
    fig, ax = plt.subplots()
    # this locator puts ticks at regular intervals
    loc = ticker.MultipleLocator(base=0.2)
    ax.yaxis.set_major_locator(loc)
    plt.plot(points)

In [17]:
def evaluate(encoder, decoder, sentence, max_length=MAX_LENGTH):
    with torch.no_grad():
        input_tensor = tensorFromSentence(input_lang, sentence)
        input_length = input_tensor.size()[0]
        encoder_hidden = encoder.initHidden()

        encoder_outputs = torch.zeros(max_length, encoder.hidden_size, device=device)

        for ei in range(input_length):
            encoder_output, encoder_hidden = encoder(input_tensor[ei],
                                                     encoder_hidden)
            encoder_outputs[ei] += encoder_output[0, 0]

        decoder_input = torch.tensor([[SOS_token]], device=device)  # SOS

        decoder_hidden = encoder_hidden

        decoded_words = []
        decoder_attentions = torch.zeros(max_length, max_length)

        for di in range(max_length):
            decoder_output, decoder_hidden, decoder_attention = decoder(
                decoder_input, decoder_hidden, encoder_outputs)
            decoder_attentions[di] = decoder_attention.data
            topv, topi = decoder_output.data.topk(1)
            if topi.item() == EOS_token:
                decoded_words.append('<EOS>')
                break
            else:
                decoded_words.append(output_lang.index2word[topi.item()])

            decoder_input = topi.squeeze().detach()

        return decoded_words, decoder_attentions[:di + 1]


In [18]:
def evaluateRandomly(encoder, decoder, n=10):
    for i in range(n):
        pair = random.choice(pairs)
        print('>', pair[0])
        print('=', pair[1])
        output_words, attentions = evaluate(encoder, decoder, pair[0])
        output_sentence = ' '.join(output_words)
        print('<', output_sentence)
        print('')


In [158]:
hidden_size = 256
encoder1 = EncoderRNN(input_lang.n_words, hidden_size).to(device)
attn_decoder1 = AttnDecoderRNN(hidden_size, output_lang.n_words, dropout_p=0.1).to(device)

trainIters(encoder1, attn_decoder1, 75000, print_every=1000)


tensor([[[-0.3704,  0.0000, -0.1272, -1.2708,  0.8873,  0.5905, -0.6304,
           2.6122, -0.2201, -0.4545,  3.0452, -1.0709,  0.6694,  0.1171,
          -1.1367,  1.1170, -0.0842, -0.3841,  1.4449,  0.7285,  1.1220,
          -1.1737,  0.0000, -0.9539, -0.1947, -1.7215, -0.1806, -1.9575,
          -0.9190,  1.1934, -1.2883, -0.0000,  0.5160, -1.2330,  0.0672,
           1.8065,  1.4007,  0.1292,  0.0160,  0.2517, -0.2561, -0.4580,
           0.9771, -0.4131,  0.3248, -0.4851,  2.2207,  1.5582,  0.2549,
          -0.4040, -0.2332, -1.2933,  0.0940,  0.8398, -0.7917, -1.0122,
           0.9685,  0.0940,  0.0282,  0.5363, -1.1492,  0.5223, -1.1336,
           0.5806, -0.3758, -0.7145, -0.3013,  0.8452,  0.2078,  0.6743,
           1.6886, -0.7618, -0.3132, -0.9993, -0.4097, -0.2715, -0.9820,
           1.4352,  0.6417, -1.3280, -1.4331, -2.2983,  1.7102, -0.6304,
          -0.9867, -1.1386, -1.1891,  0.0444,  2.4467, -0.0176,  0.2828,
           0.9739,  1.0385,  0.0000, -2.5164, -0.62

tensor([[[-0.3703,  0.4228, -0.1273, -1.2707,  0.8873,  0.5906, -0.6302,
           2.6123, -0.2202, -0.4545,  3.0451, -1.0709,  0.6694,  0.1172,
          -1.1367,  1.1170, -0.0843, -0.3841,  1.4449,  0.7285,  0.0000,
          -1.1738,  0.3496, -0.9540, -0.1948, -1.7216, -0.1806, -1.9576,
          -0.9191,  1.1935, -1.2883, -2.0976,  0.5159, -1.2330,  0.0672,
           0.0000,  1.4007,  0.1292,  0.0159,  0.2518, -0.2563, -0.4580,
           0.9770, -0.4131,  0.3248, -0.4852,  2.2207,  1.5582,  0.0000,
          -0.4040, -0.2331, -0.0000,  0.0941,  0.8398, -0.7917, -1.0123,
           0.9686,  0.0941,  0.0283,  0.5364, -1.1492,  0.5224, -0.0000,
           0.5805, -0.3759, -0.7144, -0.3014,  0.8452,  0.2078,  0.0000,
           1.6884, -0.7617, -0.3132, -0.9994, -0.4097, -0.2715, -0.9819,
           1.4353,  0.6419, -1.3282, -1.4332, -2.2982,  1.7103, -0.6304,
          -0.9866, -1.1388, -1.1892,  0.0444,  2.4468, -0.0177,  0.0000,
           0.9738,  1.0386,  0.2679, -2.5164, -0.62

tensor([[[-0.3705,  0.4227, -0.1275, -1.2707,  0.8874,  0.5907, -0.6300,
           2.6125, -0.2203, -0.4546,  3.0451, -1.0708,  0.6692,  0.1173,
          -1.1367,  1.1171, -0.0845, -0.3842,  1.4450,  0.7285,  1.1222,
          -1.1739,  0.3497, -0.9540, -0.1949, -1.7217, -0.1808, -1.9577,
          -0.9190,  1.1936, -1.2885, -0.0000,  0.0000, -1.2331,  0.0672,
           1.8064,  1.4009,  0.1291,  0.0157,  0.2519, -0.2564, -0.4579,
           0.9770, -0.4133,  0.3247, -0.4853,  2.2209,  1.5583,  0.2551,
          -0.0000, -0.2331, -1.2932,  0.0940,  0.8400, -0.7917, -1.0123,
           0.9687,  0.0942,  0.0282,  0.5364, -1.1494,  0.5225, -1.1336,
           0.5805, -0.3760, -0.7143, -0.3013,  0.8452,  0.2078,  0.6742,
           1.6881, -0.7618, -0.3133, -0.9995, -0.4097, -0.2717, -0.9818,
           0.0000,  0.6421, -1.3284, -1.4331, -2.2982,  1.7104, -0.6306,
          -0.9867, -1.1390, -1.1892,  0.0444,  2.4470, -0.0177,  0.0000,
           0.9737,  1.0386,  0.2676, -2.5166, -0.62

tensor([[[-0.3705,  0.4226, -0.1277, -1.2709,  0.8874,  0.5907, -0.6299,
           2.6127, -0.2205, -0.4546,  3.0452, -1.0708,  0.6691,  0.1173,
          -1.1367,  1.1171, -0.0846, -0.3843,  1.4451,  0.7285,  1.1222,
          -1.1740,  0.3497, -0.9540, -0.1950, -0.0000, -0.0000, -1.9579,
          -0.9190,  1.1938, -1.2886, -0.0000,  0.5155, -1.2332,  0.0672,
           1.8063,  1.4010,  0.1290,  0.0157,  0.2519, -0.2567, -0.4578,
           0.9771, -0.4133,  0.3247, -0.0000,  2.2210,  1.5585,  0.0000,
          -0.4038, -0.2331, -1.2932,  0.0938,  0.8400, -0.7917, -1.0123,
           0.9688,  0.0943,  0.0282,  0.5364, -1.1496,  0.5225, -1.1337,
           0.5805, -0.3761, -0.7143, -0.3012,  0.8452,  0.2077,  0.6742,
           1.6880, -0.7618, -0.3133, -0.9997, -0.4097, -0.2719, -0.9819,
           0.0000,  0.6424, -1.3285, -1.4331, -2.2984,  0.0000, -0.6307,
          -0.9868, -1.1392, -1.1892,  0.0444,  2.4472, -0.0175,  0.2827,
           0.0000,  1.0386,  0.2675, -2.5167, -0.62

tensor([[[-0.3704,  0.4225, -0.1277, -1.2709,  0.0000,  0.5908, -0.6299,
           0.0000, -0.0000, -0.4546,  3.0452, -1.0706,  0.6691,  0.1172,
          -1.1368,  1.1171, -0.0846, -0.3843,  1.4451,  0.7284,  1.1223,
          -1.1740,  0.3498, -0.9541, -0.1951, -1.7218, -0.1811, -1.9580,
          -0.9191,  1.1938, -1.2886, -2.0977,  0.5153, -1.2332,  0.0671,
           1.8063,  1.4010,  0.1291,  0.0157,  0.2519, -0.2566, -0.4576,
           0.9771, -0.4133,  0.3246, -0.4854,  2.2209,  1.5585,  0.2552,
          -0.4038, -0.2330, -1.2932,  0.0938,  0.8400, -0.7917, -1.0123,
           0.9688,  0.0945,  0.0282,  0.5364, -1.1497,  0.5224, -1.1337,
           0.5806, -0.3764, -0.7142, -0.3013,  0.8452,  0.2077,  0.6742,
           0.0000, -0.7618, -0.3134, -0.9998, -0.4097, -0.2718, -0.9819,
           1.4356,  0.6423, -1.3286, -1.4331, -2.2984,  1.7105, -0.6307,
          -0.9867, -1.1392, -0.0000,  0.0445,  2.4473, -0.0176,  0.2828,
           0.9735,  1.0388,  0.2673, -2.5169, -0.62

...

tensor([[[-0.3724,  0.4221, -0.0000, -1.2759,  0.8885,  0.5918, -0.6297,
           0.0000, -0.2203, -0.4547,  3.0507, -0.0000,  0.6680,  0.1156,
          -0.0000,  1.1169, -0.0866, -0.3852,  1.4479,  0.7286,  1.1254,
          -1.1768,  0.3508, -0.9566, -0.1969, -1.7248, -0.1839, -1.9643,
          -0.9187,  0.0000, -0.0000, -2.1020,  0.5135, -1.2356,  0.0674,
           1.8093,  1.4050,  0.1298,  0.0151,  0.2536, -0.2608, -0.4580,
           0.0000, -0.4141,  0.3243, -0.0000,  0.0000,  1.5627,  0.2577,
          -0.4021, -0.2335, -1.2956,  0.0909,  0.8434, -0.7944, -0.0000,
           0.9713,  0.0985,  0.0290,  0.5379, -1.1552,  0.5246, -1.1360,
           0.5820, -0.3798, -0.7158, -0.3024,  0.8466,  0.2077,  0.6742,
           1.6878, -0.0000, -0.3140, -1.0034, -0.4095, -0.2741, -0.9832,
           1.4392,  0.0000, -1.3340, -1.4377, -2.3027,  1.7170, -0.6338,
          -0.9896, -1.1428, -1.1932,  0.0447,  2.4548, -0.0170,  0.2830,
           0.9744,  1.0417,  0.2648, -2.5220, -0.62

tensor([[[-0.3724,  0.4222, -0.1301, -1.2760,  0.8885,  0.5919, -0.6298,
           2.6206, -0.2203, -0.0000,  0.0000, -1.0706,  0.6681,  0.1155,
          -0.0000,  1.1169, -0.0866, -0.3852,  0.0000,  0.7286,  1.1255,
          -1.1769,  0.3508, -0.9567, -0.1969, -1.7248, -0.1839, -1.9644,
          -0.9186,  1.1985, -1.2924, -2.1021,  0.5135, -1.2356,  0.0674,
           1.8094,  1.4050,  0.1298,  0.0000,  0.2536, -0.2608, -0.4580,
           0.9784, -0.4141,  0.3243, -0.4877,  2.2247,  0.0000,  0.0000,
          -0.4021, -0.2335, -0.0000,  0.0909,  0.8434, -0.7943, -1.0161,
           0.9714,  0.0985,  0.0290,  0.5379, -1.1552,  0.0000, -1.1360,
           0.5821, -0.3799, -0.7158, -0.3024,  0.8466,  0.2077,  0.6743,
           1.6878, -0.7636, -0.3140, -1.0035, -0.4095, -0.2740, -0.9833,
           1.4392,  0.6460, -1.3340, -1.4378, -2.3027,  1.7170, -0.6339,
          -0.9897, -1.1428, -1.1933,  0.0447,  2.4548, -0.0170,  0.2830,
           0.9744,  1.0417,  0.2648, -2.5220, -0.62

tensor([[[-0.0000,  0.4222, -0.1301, -0.0000,  0.0000,  0.5918, -0.6297,
           2.6205, -0.2203, -0.4546,  3.0507, -1.0706,  0.6680,  0.1156,
          -1.1412,  1.1169, -0.0866, -0.3852,  1.4479,  0.7286,  1.1255,
          -1.1768,  0.3508, -0.0000, -0.1969, -0.0000, -0.1839, -1.9643,
          -0.9187,  1.1984, -1.2924, -2.1020,  0.5136, -1.2356,  0.0674,
           1.8093,  1.4050,  0.1298,  0.0150,  0.0000, -0.0000, -0.4580,
           0.9784, -0.4141,  0.3243, -0.0000,  2.2246,  1.5627,  0.2577,
          -0.4021, -0.2334, -1.2956,  0.0909,  0.8434, -0.7944, -1.0161,
           0.9713,  0.0984,  0.0290,  0.5378, -1.1552,  0.5246, -0.0000,
           0.5821, -0.3798, -0.7158, -0.3024,  0.8466,  0.2077,  0.6742,
           1.6878, -0.7636, -0.3140, -1.0035, -0.4095, -0.2741, -0.0000,
           1.4392,  0.6459, -1.3340, -1.4377, -2.3027,  1.7170, -0.6339,
          -0.9896, -1.1428, -1.1932,  0.0447,  0.0000, -0.0170,  0.2829,
           0.9744,  1.0417,  0.2648, -0.0000, -0.62

tensor([[[-0.3723,  0.4222, -0.1300, -1.2759,  0.8885,  0.5918, -0.6297,
           2.6204, -0.2203, -0.4546,  3.0507, -1.0705,  0.6680,  0.1156,
          -1.1413,  0.0000, -0.0866, -0.3853,  1.4479,  0.7286,  1.1255,
          -1.1767,  0.3507, -0.0000, -0.1969, -1.7247, -0.1838, -1.9642,
          -0.9187,  1.1984, -1.2924, -2.1019,  0.5137, -1.2356,  0.0673,
           0.0000,  1.4050,  0.1297,  0.0150,  0.2536, -0.2607, -0.4581,
           0.9784, -0.4141,  0.0000, -0.4876,  2.2247,  1.5626,  0.2576,
          -0.4021, -0.2334, -1.2957,  0.0909,  0.8433, -0.0000, -1.0161,
           0.9713,  0.0984,  0.0290,  0.5379, -1.1552,  0.5246, -1.1361,
           0.5820, -0.0000, -0.7158, -0.3025,  0.0000,  0.2077,  0.0000,
           0.0000, -0.7635, -0.3141, -1.0034, -0.4095, -0.2740, -0.9833,
           1.4391,  0.6460, -1.3341, -0.0000, -2.3026,  0.0000, -0.6338,
          -0.9896, -1.1427, -1.1932,  0.0448,  2.4547, -0.0000,  0.2829,
           0.9744,  1.0416,  0.0000, -2.5219, -0.62

KeyboardInterrupt: 

In [131]:
evaluateRandomly(encoder1, attn_decoder1)

> je suis celui qui a construit ceci .
= i m the one who built this .
< i m the one who built this . <EOS>

> elle est folle .
= she s demented .
< she is demented . <EOS>

> je suis fatigue de faire la queue .
= i m tired of waiting in line .
< i m tired of waiting . <EOS>

> je m amuse vraiment .
= i m actually enjoying myself .
< i m making my myself . <EOS>

> elle est en train de pleurer .
= she is crying .
< she is crying . <EOS>

> tu vas le regretter .
= you re going to regret this .
< you re going to regret this . <EOS>

> je suis un peu decu .
= i m a little disappointed .
< i m a little disappointed . <EOS>

> je suis tres gros .
= i m very fat .
< i am very fat . <EOS>

> j ai peur de me noyer .
= i m afraid of drowning .
< i m afraid i ve back . <EOS>

> je m amuse comme un fou .
= i m having the time of my life .
< i m having the time of my life . <EOS>



In [132]:
output_words, attentions = evaluate(
    encoder1, attn_decoder1, "je suis trop froid .")
plt.matshow(attentions.numpy())


In [133]:
def showAttention(input_sentence, output_words, attentions):
    # Set up figure with colorbar
    fig = plt.figure()
    ax = fig.add_subplot(111)
    cax = ax.matshow(attentions.numpy(), cmap='bone')
    fig.colorbar(cax)

    # Set up axes
    ax.set_xticklabels([''] + input_sentence.split(' ') +
                       ['<EOS>'], rotation=90)
    ax.set_yticklabels([''] + output_words)

    # Show label at every tick
    ax.xaxis.set_major_locator(ticker.MultipleLocator(1))
    ax.yaxis.set_major_locator(ticker.MultipleLocator(1))

    plt.show()


def evaluateAndShowAttention(input_sentence):
    output_words, attentions = evaluate(
        encoder1, attn_decoder1, input_sentence)
    print('input =', input_sentence)
    print('output =', ' '.join(output_words))
    showAttention(input_sentence, output_words, attentions)


evaluateAndShowAttention("elle a cinq ans de moins que moi .")

evaluateAndShowAttention("elle est trop petit .")

evaluateAndShowAttention("je ne crains pas de mourir .")

evaluateAndShowAttention("c est un jeune directeur plein de talent .")

input = elle a cinq ans de moins que moi .
output = she s five years younger than i am . <EOS>
input = elle est trop petit .
output = she is too short . <EOS>
input = je ne crains pas de mourir .
output = i m not going to die . <EOS>
input = c est un jeune directeur plein de talent .
output = he s a talented young talented . <EOS>
